# DeepDrug3D

In [1]:
import numpy as np

from sklearn.preprocessing import LabelEncoder
from keras.models import Sequential
from keras import optimizers
from keras.layers import Dense, Flatten, TimeDistributedn, Dropout
from keras import Input, Model
from keras.layers import add, Activation
#from keras.utils import plot_model  # Needs pydot.
from keras.layers import Conv3D, MaxPooling3D

Using TensorFlow backend.


## Create pocket lists
4 pockets are created :
  + control
  + steroid
  + heme
  + nucleotide

In [2]:
with open("control.list", "r") as filin:
    control = filin.read()
control = control.split("\n")
control.pop()

with open("steroid.list", "r") as filin:
    steroid = filin.read()
steroid = steroid.split("\n")
steroid.pop()

with open("heme.list", "r") as filin:
    heme = filin.read()
heme = heme.split("\n")
heme.pop()

with open("nucleotide.list", "r") as filin:
    nucleotide = filin.read()
nucleotide = nucleotide.split("\n")
nucleotide.pop()

''

### Creating input and ouputs

In [3]:
data_onehot = np.ndarray(shape=(2219, 14, 32, 32, 32)) # initializing empty array
indices = np.random.permutation(2219)
output = np.ndarray(shape=(2219, 3)) # softmax 3, {steroid=1, heme=1, nucleotide=1}
lmin = len(steroid)
lmid = len(heme)
lmax = len(nucleotide)

In [4]:
n = -1
for i in indices:
    n += 1
    if i < lmin:
        data_onehot[n,] = np.load("deepdrug3d_voxel_data/"+steroid[i]+".npy")
        output[n,] = [1,0,0]
    elif i > lmin and i < (lmin + lmid):
        data_onehot[n,] = np.load("deepdrug3d_voxel_data/"+heme[i - lmin]+".npy")
        output[n,] = [0,1,0]
    else:
        data_onehot[n,] = np.load("deepdrug3d_voxel_data/"+nucleotide[i - (lmin+lmid) - 1]+".npy")
        output[n,] = [0,0,1]

In [5]:
X_train = data_onehot[0:1664,]
Y_train = output[0:1664,]
X_test = data_onehot[1664:,]
Y_test = output[1664:,]

In [14]:
def model_sequential(): # créer un objet modèle
    """
    Return a simple sequentiel model
    
    Returns :
        - model : keras.Model
    """
    inputs = Input(shape=(32,32,32,14)) # 759 aa, 21 car onehot
    conv_1 = Conv3D(64, (28, 28, 28), padding="same", activation="LeakyReLU",
                        kernel_initializer="he_normal")(inputs)
    conv_2 = Conv3D(64, (26, 26, 26), padding="same", activation="LeakyReLU",
                        kernel_initializer="he_normal")(conv_1)
    drop_1 = Dropout(0.2)(conv_2)
    maxpool = MaxPooling3D()(drop_1)
    drop_2 = Dropout(0.4)(maxpool)
    dense = Dense(512)(drop_2)
    drop_3 = Dropout(0.4)(dense)
    output = TimeDistributed(Dense(3, activation='softmax'))(drop_3)
    model = Model(inputs=inputs, outputs=output)
    my_opt = optimizers.Adam(learning_rate=0.000001, beta_1=0.9, beta_2=0.999, amsgrad=False)
    print(model.summary)
    model.compile(optimizer=my_opt, loss="categorical_crossentropy",
                  metrics=["accuracy"])
    return model

(1, 14, 32, 32, 32)